# Anomaly detection using neural networks

In [69]:
import numpy as np
import pandas as pd

import plotly.graph_objects as go

import tensorflow as tf
from tensorflow.keras import backend as K
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import *
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.losses import MeanSquaredError
from tensorflow.keras.metrics import RootMeanSquaredError
from tensorflow.keras.optimizers import Adam

from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error

INPUT_FILE_PATH="data/cesnet-time-series24"

# Network Traffic Using Forecasting
 
In this python notebook, I wanted to test or improve the provided reference implementation for **LSTM networks** from python notebook `NECS2025-Network-Traffic-Forecasting.ipynb`. I tried different settings for the model and some minor changes like automatically adjusting the time window, z-score selection for each metric, improved results graph visualization etc.

Explanation of data processing and detection:

1. **Data Loading & Preprocessing:** Function `load_series()` loads the time series data for a specific metric and fills in missing time steps with default `fill_missing()`.
2. **Data Splitting:** Splits the dataset into training, training and test data. The training/validation splits are adjusted to include overlap (`train_window`).
3. **Window Generation & Normalization:** `adaptive_train_window()` chooses a dynamic training window size based on the standard deviation of the time series. High variance = smaller window, low variance = larger window. `prepare_data()` normalizes the train, validation, and test sets using `StandardScaler`. Converts each into overlapping time windows using `df_to_X_y()` for model input.
4. **Model Training:** Constructs LSTM model using `get_model()` and saves the best model. Uses `prepare_predictions()` to inverse transform predictions, compute residuals, and detect anomalies. For anomaly detection is used dynamic confidence interval. A value is marked as anomalous when it exceeds a certain threshold.
5. **Evaluation & Visualization:** Calculates _RMSE_, _SMAPE_, and $R^2$ for all predictions. The results are displayed on an interactive graph with dates on the X-axis.

The results are not always accurate. Some metrics can be better predicted than others which can be seen in the results and evaluation scores. Very heterogeneous values in the data are generally difficult to predict. Furthermore, from personal experience, I have to point out that neural networks are not exactly my cup of tea.

In [70]:
# Definitions of help functions and classes

def load_series(input_file_path:str, aggregation_rate:str, aggregation_level:str, data_id=int) -> pd.DataFrame:
    # Load times
    time_ids = pd.read_csv(f"{input_file_path}/times/times_{aggregation_rate[4:]}.csv")
    time_ids['time'] = pd.to_datetime(time_ids['time']) # convert time to datetime
    time_map = dict(zip(time_ids['id_time'], time_ids['time']))

    # Load data series
    df = pd.read_csv(f"{input_file_path}/{aggregation_level}/{aggregation_rate}/{str(data_id)}.csv")
    df = fill_missing(df, time_ids['id_time'])
    df['time'] = df['id_time'].map(time_map)
    return df


def fill_missing(train_df, train_time_ids):
    df_missing = pd.DataFrame(columns=train_df.columns)
    df_missing.id_time = train_time_ids[~train_time_ids.isin(train_df.id_time)].values

    for column in train_df.columns:
        if column == "id_time":
            continue
        if column in ["tcp_udp_ratio_packets","tcp_udp_ratio_bytes","dir_ratio_packets","dir_ratio_bytes"]:
            df_missing[column] = 0.5
        else:
            df_missing[column] = 0 # train_df[column].mean()

    return pd.concat([train_df, df_missing]).sort_values(by="id_time").reset_index()[train_df.columns]


def df_to_X_y(data, train_window, predict_window, step_size=1):
    X = []
    y = []
    for i in range(0, len(data)-train_window-predict_window, step_size):
        row = [[a] for a in data[i:i+train_window]]
        X.append(row)
        label = data[i+train_window:i+train_window+predict_window]
        y.append(label)
    return np.array(X), np.array(y)


def split_data(data:pd.DataFrame, train_window):
    data_len = len(data)
    train_piece = int(data_len * 0.5) # 50% training
    val_piece = int(data_len * 0.2)  # 20% validation
    return data[:train_piece], data[train_piece - train_window : train_piece + val_piece], data[train_piece + val_piece - train_window :]


def adaptive_train_window(series:pd.Series):
    std_values = [np.std(series[i-24:i]) for i in range(24, len(series))]
    low_threshold = np.percentile(std_values, 25)
    high_threshold = np.percentile(std_values, 75)

    std_dev = np.std(series)
    if std_dev > high_threshold:
        return 24 * 15      # Short train window with high variability
    elif std_dev < low_threshold:
        return 24 * 31 * 2  # Larger train window with high variability
    else:
        return 24 * 31
    

def smape(y_true, y_pred):
    numerator = np.abs(y_true - y_pred)
    denominator = (np.abs(y_true) + np.abs(y_pred)) / 2
    smape_value = np.mean(numerator / denominator) * 100
    return smape_value


def r2_score(y_true, y_pred):
    if len(y_true) != len(y_pred):
        raise ValueError("The lengths of y_true and y_pred must be equal.")

    y_true = np.array(y_true)
    y_pred = np.array(y_pred)

    # Total sum of squares (TSS)
    ss_total = np.sum((y_true - np.mean(y_true)) ** 2)

    # Residual sum of squares (RSS)
    ss_residual = np.sum((y_true - y_pred) ** 2)

    # R² score calculation
    r2 = 1 - (ss_residual / ss_total)

    return r2


def get_eval_metrics_df(results):
    """ Creates RMSE, SMAPE and R^2 evaluation metrics for results. """
    metrics = list(results.keys())
    index = ["Train Not-Inversed", "Train Inversed", "Validation Not-Inversed", "Validation Inversed", "Test Not-Inversed", "Test Inversed"]
    colnames = ["RMSE", "SMAPE", "R^2"]

    metrics_dfs = []
    for metric in metrics:

        train_results = results[metric]['train_results']
        val_results = results[metric]['val_results']
        test_results = results[metric]['test_results']

        df = pd.DataFrame([
            [mean_squared_error(train_results['Predictions'], train_results['Actuals']), smape(train_results['Predictions'], train_results['Actuals']), r2_score(train_results['Predictions'], train_results['Actuals'])],
            [mean_squared_error(train_results['Predictions - Inversed'], train_results['Actuals - Inversed']), smape(train_results['Predictions - Inversed'], train_results['Actuals - Inversed']), r2_score(train_results['Predictions - Inversed'], train_results['Actuals - Inversed'])],
            [mean_squared_error(val_results['Predictions'], val_results['Actuals']), smape(val_results['Predictions'], val_results['Actuals']), r2_score(val_results['Predictions'], val_results['Actuals'])],
            [mean_squared_error(val_results['Predictions - Inversed'], val_results['Actuals - Inversed']), smape(val_results['Predictions - Inversed'], val_results['Actuals - Inversed']), r2_score(val_results['Predictions - Inversed'], val_results['Actuals - Inversed'])],
            [mean_squared_error(test_results['Predictions'], test_results['Actuals']), smape(test_results['Predictions'], test_results['Actuals']), r2_score(test_results['Predictions'], test_results['Actuals'])],
            [mean_squared_error(test_results['Predictions - Inversed'], test_results['Actuals - Inversed']), smape(test_results['Predictions - Inversed'], test_results['Actuals - Inversed']), r2_score(test_results['Predictions - Inversed'], test_results['Actuals - Inversed'])]
        ], index=index, columns=colnames)
        metrics_dfs.append(df)

    df = pd.concat(metrics_dfs, axis=1)
    df.columns = pd.MultiIndex.from_product([metrics, colnames], names=["Metrics", "Evaluation metrics"])
    return df


In [71]:
def prepare_data(metric, train_df, val_df, test_df, train_window, predict_window, scale=True):
    train_data = train_df[metric].to_numpy()
    val_data = val_df[metric].to_numpy()
    test_data = test_df[metric].to_numpy()

    if scale is True:
        scaler = StandardScaler()
        train_data = scaler.fit_transform(train_data.reshape(len(train_data),1)).reshape(1, len(train_data))[0]
        val_data = scaler.transform(val_data.reshape(len(val_data),1)).reshape(1, len(val_data))[0]
        test_data = scaler.transform(test_data.reshape(len(test_data),1)).reshape(1, len(test_data))[0]
    else:
        scaler = None

    X_train, y_train = df_to_X_y(train_data, train_window, predict_window)
    X_val, y_val = df_to_X_y(val_data, train_window, predict_window)
    X_test, y_test = df_to_X_y(test_data, train_window, predict_window, step_size=predict_window)

    return X_train, y_train, X_val, y_val, X_test, y_test, scaler


def prepare_predictions(train_predictions, val_predictions, test_predictions, y_train, y_val, y_test,  scaler, z = 10, window_size = 24*7):
    train_results = pd.DataFrame(data={'Predictions':train_predictions, 'Actuals':y_train.flatten()})
    val_results = pd.DataFrame(data={'Predictions':val_predictions, 'Actuals':y_val.flatten()})
    test_results = pd.DataFrame(data={'Predictions':test_predictions, 'Actuals':y_test.flatten()})
    if scaler is not None:
        train_results['Predictions - Inversed'] = scaler.inverse_transform(train_results['Predictions'].to_numpy().reshape(1, -1))[0]
        train_results['Actuals - Inversed'] = scaler.inverse_transform(train_results['Actuals'].to_numpy().reshape(1, -1))[0]
        val_results['Predictions - Inversed'] = scaler.inverse_transform(val_results['Predictions'].to_numpy().reshape(1, -1))[0]
        val_results['Actuals - Inversed'] = scaler.inverse_transform(val_results['Actuals'].to_numpy().reshape(1, -1))[0]
        test_results['Predictions - Inversed'] = scaler.inverse_transform(test_results['Predictions'].to_numpy().reshape(1, -1))[0]
        test_results['Actuals - Inversed'] = scaler.inverse_transform(test_results['Actuals'].to_numpy().reshape(1, -1))[0]

    anomalies = []
    # Calculate dynamic stable confidence intervals
    for i in range(window_size, len(test_results['Predictions - Inversed'])):
        if i < window_size:
            squared_residuids = abs(test_results['Actuals - Inversed'][:window_size] - test_results['Predictions - Inversed'][:window_size])
            sigma = squared_residuids.std()
            _mean = squared_residuids.mean()
        else:
            squared_residuids = abs(test_results['Actuals - Inversed'][i-window_size:i] - test_results['Predictions - Inversed'][i-window_size:i])
            sigma = squared_residuids.std()
            _mean = squared_residuids.mean()

        threshold = _mean + z * sigma

        if abs(test_results['Actuals - Inversed'][i] - test_results['Predictions - Inversed'][i]) > threshold:
            anomalies.append(i)

    return train_results, val_results, test_results, anomalies


def train_model(df, metric, get_model, num_epochs, name, z_score=5, window_size=24*7):
    train_window = adaptive_train_window(df[metric])
    predict_window = 1
    train_df, val_df, test_df = split_data(df, train_window)
    X_train, y_train, X_val, y_val, X_test, y_test, scaler = prepare_data(metric, train_df, val_df, test_df, train_window, predict_window, scale=True)
    cp1 = ModelCheckpoint(f'model/model_checkpoint_{name}.keras', save_best_only=True)

    while True:
        model = get_model(train_window, predict_window)
        history = model.fit(X_train, y_train, validation_data=(X_val, y_val), epochs=num_epochs, callbacks=[cp1])  # 3-4 min run
        if np.isnan(history.history['loss']).any():
            pass
        else:
            break

    train_predictions = model.predict(X_train).flatten()
    val_predictions = model.predict(X_val).flatten()
    test_predictions = model.predict(X_test).flatten()
    train_results, val_results, test_results, outliers = prepare_predictions(train_predictions, val_predictions, test_predictions, y_train, y_val, y_test, scaler, z_score, window_size)

    # Times for plotting 
    test_times = df['time'][len(df) - len(y_test):].reset_index()['time']

    result = {
        "train_results": train_results,
        "val_results": val_results,
        "test_results": test_results,
        "outliers": outliers,
        "scaler": scaler,
        "test_times": test_times
    }

    return result


def show_prediction_graphs(results):
    metrics = list(results.keys())
    initial_metric = metrics[0]  # Show first metric initially
    
    # Create figure
    fig = go.Figure()
    
    # Add actual values trace
    for metric in metrics:
        fig.add_trace(go.Scatter(
            x=results[metric]['test_times'],
            y=results[metric]['test_results']['Actuals - Inversed'],
            mode='lines',
            name=f'Actual - {metric}',
            visible=(metric == initial_metric)
        ))
        
        # Add predicted values trace
        fig.add_trace(go.Scatter(
            x=results[metric]['test_times'],
            y=results[metric]['test_results']['Predictions - Inversed'],
            mode='lines',
            name=f'Predicted - {metric}',
            visible=(metric == initial_metric)
        ))
        
        # Add anomaly points
        fig.add_trace(go.Scatter(
            x=results[metric]['test_times'].iloc[results[metric]['outliers']],
            y=results[metric]['test_results']['Actuals - Inversed'].iloc[results[metric]['outliers']],
            mode='markers',
            marker=dict(color='red', size=8),
            name=f'Anomalies - {metric}',
            visible=(metric == initial_metric)
        ))
    
    # Create dropdown buttons
    buttons = []
    for i, metric in enumerate(metrics):
        visibility = [False] * (3 * len(metrics))  # Each metric has 3 traces
        visibility[i*3:i*3+3] = [True, True, True]  # Set only this metric visible
        
        buttons.append(dict(
            label=metric,
            method='update',
            args=[{'visible': visibility}, {'title': f"Results/Predictions for {metric}"}]
        ))
    
    # Update layout with dropdown
    fig.update_layout(
        title=f'Predictions for {initial_metric}',
        updatemenus=[{
            "buttons": buttons,
            "direction": "down",
            "showactive": True,
        }],
        xaxis_title="Time",
        yaxis_title="Value"
    )    
    fig.show()

In [72]:
def get_model(train_window, predict_window):
    # Model definition (DON'T TOUCH)
    model = Sequential()
    model.add(InputLayer((train_window, 1)))

    #model.add(LSTM(64 * predict_window))
    model.add(LSTM(128 * predict_window))

    model.add(Dense(16 * predict_window, 'relu'))
    #model.add(Dense(32 * predict_window, 'relu'))
    #model.add(Dense(16 * predict_window, 'relu'))
    #model.add(Dense(32 * predict_window, 'relu'))


    # Last prediction layer (DON'T TOUCH)
    model.add(Dense(predict_window, 'linear'))

    #LEARNING_RATE=0.1
    #LEARNING_RATE=0.01
    LEARNING_RATE=0.001
    #LEARNING_RATE=0.0001

    model.compile(loss=MeanSquaredError(), optimizer=Adam(learning_rate=LEARNING_RATE), metrics=[RootMeanSquaredError()])
    return model


# Examples

To use the method, just specify what _institution_/_subnet_/_ip_ and _identifier_ will be analyzed. Then just load the time series using the `load_series()` function, select the number of **epochs**, **the metrics in which to analyzed for anomalies**, and **the z-score for each metric**. The z-score determines the confidence interval and affects the amount of anomalies detected (e.g., $ z=8 $ for 99.2% confidence).

Then it is possible to train the model for each metric and its z-score in a loop and view the results graphically. The evaluation results can be written using the `get_eval_metrics_df()` function.

In [73]:
AGG_RATE = "agg_1_hour"
AGG_LEVEL = "institutions" # can be institutions or institution_subnets or ip_addresses_sample

# Subnet 36

In [ ]:
AGG_LEVEL = "institution_subnets" # can be institutions or institution_subnets or ip_addresses_sample
DATA_ID = 36

df:pd.DataFrame = load_series(INPUT_FILE_PATH, AGG_RATE, AGG_LEVEL, DATA_ID)

NUM_EPOCHS=5

metrics = ['n_packets', 'n_bytes', 'sum_n_dest_ip', 'sum_n_dest_asn', 'sum_n_dest_ports', 'dir_ratio_packets', 'avg_duration']
z_scores = [8,8,5,10,10,10,8]
results = {}
for (metric, z) in zip(metrics, z_scores):
    print(metric)
    results[metric] = train_model(df, metric, get_model, NUM_EPOCHS, f"{AGG_LEVEL}_{str(DATA_ID)}", z)

show_prediction_graphs(results)

n_packets
Epoch 1/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 14s 132ms/step - loss: 0.2983 - root_mean_squared_error: 0.5206 - val_loss: 1.3091 - val_root_mean_squared_error: 1.1441
Epoch 2/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 120ms/step - loss: 0.1355 - root_mean_squared_error: 0.3650 - val_loss: 1.3082 - val_root_mean_squared_error: 1.1438
Epoch 3/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 119ms/step - loss: 0.1822 - root_mean_squared_error: 0.4202 - val_loss: 1.3659 - val_root_mean_squared_error: 1.1687
Epoch 4/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 119ms/step - loss: 0.2146 - root_mean_squared_error: 0.4540 - val_loss: 1.3395 - val_root_mean_squared_error: 1.1574
Epoch 5/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 120ms/step - loss: 0.1203 - root_mean_squared_error: 0.3450 - val_loss: 1.4076 - val_root_mean_squared_error: 1.1864
94/94 ━━━━━━━━━━━━━━━━━━━━ 4s 37ms/step
42/42 ━━━━━━━━━━━━━━━━━━━━ 2s 36ms/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 2s 36ms/step
n_bytes
Epoch 1/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 13s 124ms/step - loss: 0.0793 - roo

In [75]:
# Evaluation metrics table

eval_metrics_df = get_eval_metrics_df(results)

pd.options.display.width = 0  # Prevent line wrapping
pd.options.display.max_columns = None  # Show all columns
pd.options.display.float_format = "{:.2f}".format  # Format floats with 2 decimal places
print(eval_metrics_df.to_string(index=True))


Metrics                        n_packets                             n_bytes               sum_n_dest_ip            sum_n_dest_asn            sum_n_dest_ports            dir_ratio_packets            avg_duration           
Evaluation metrics                  RMSE SMAPE    R^2                   RMSE  SMAPE    R^2          RMSE SMAPE  R^2           RMSE SMAPE  R^2             RMSE SMAPE  R^2              RMSE SMAPE  R^2         RMSE SMAPE  R^2
Train Not-Inversed                  0.15 52.36  -1.78                   0.07  50.34  -7.29          0.09 62.85 0.92           0.13 60.60 0.84             0.32 72.26 0.60              0.14 58.29 0.82         0.22 69.35 0.74
Train Inversed           148572493286.55 45.47  -1.78  110454872065872016.00  73.27  -7.29    3601038.34  8.44 0.92      528517.48  7.33 0.84       1263077.24  9.22 0.60              0.00  2.60 0.82         0.32  6.73 0.74
Validation Not-Inversed             1.41 74.58  -3.47                   1.04  78.21 -11.83          0.03 58.

# Subnet 38

In [ ]:
AGG_LEVEL = "institution_subnets" # can be institutions or institution_subnets or ip_addresses_sample
DATA_ID = 38

df:pd.DataFrame = load_series(INPUT_FILE_PATH, AGG_RATE, AGG_LEVEL, DATA_ID)

NUM_EPOCHS=5

metrics = ['n_packets', 'n_bytes', 'sum_n_dest_ip', 'sum_n_dest_asn', 'sum_n_dest_ports', 'dir_ratio_packets', 'avg_duration']
z_scores = [10,10,5,5,10,10,10]
results = {}
for (metric, z) in zip(metrics, z_scores):
    print(metric)
    results[metric] = train_model(df, metric, get_model, NUM_EPOCHS, f"{AGG_LEVEL}_{str(DATA_ID)}", z)

show_prediction_graphs(results)

n_packets
Epoch 1/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 12s 121ms/step - loss: 0.1476 - root_mean_squared_error: 0.3818 - val_loss: 0.1339 - val_root_mean_squared_error: 0.3660
Epoch 2/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.1374 - root_mean_squared_error: 0.3620 - val_loss: 0.1052 - val_root_mean_squared_error: 0.3243
Epoch 3/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.0690 - root_mean_squared_error: 0.2617 - val_loss: 0.1093 - val_root_mean_squared_error: 0.3305
Epoch 4/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.0628 - root_mean_squared_error: 0.2486 - val_loss: 0.1141 - val_root_mean_squared_error: 0.3378
Epoch 5/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.0793 - root_mean_squared_error: 0.2799 - val_loss: 0.1109 - val_root_mean_squared_error: 0.3331
94/94 ━━━━━━━━━━━━━━━━━━━━ 3s 36ms/step
42/42 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 2s 35ms/step
n_bytes
Epoch 1/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 12s 120ms/step - loss: 0.2193 - roo

In [77]:
# Evaluation metrics table

eval_metrics_df = get_eval_metrics_df(results)

pd.options.display.width = 0  # Prevent line wrapping
pd.options.display.max_columns = None  # Show all columns
pd.options.display.float_format = "{:.2f}".format  # Format floats with 2 decimal places
print(eval_metrics_df.to_string(index=True))


Metrics                          n_packets                              n_bytes              sum_n_dest_ip            sum_n_dest_asn            sum_n_dest_ports            dir_ratio_packets            avg_duration           
Evaluation metrics                    RMSE  SMAPE  R^2                     RMSE  SMAPE   R^2          RMSE SMAPE  R^2           RMSE SMAPE  R^2             RMSE SMAPE  R^2              RMSE SMAPE  R^2         RMSE SMAPE  R^2
Train Not-Inversed                    0.06  13.83 0.87                     0.07  12.37  0.79          0.18 58.46 0.77           0.18 59.90 0.80             0.23 68.17 0.67              0.25 72.01 0.68         0.28 78.59 0.57
Train Inversed           40507534467071.89 133.72 0.87  65360176915194241024.00 110.92  0.79    1215723.47  7.78 0.77      644144.42  7.48 0.80       2747838.88  9.74 0.67              0.00  2.00 0.68         0.23  8.49 0.57
Validation Not-Inversed               0.11  17.51 0.64                     0.12  15.62  0.37        

In [ ]:
AGG_RATE = "agg_1_hour"
AGG_LEVEL = "ip_addresses_sample" # can be institutions or institution_subnets or ip_addresses_sample
DATA_ID = 1367

df:pd.DataFrame = load_series(INPUT_FILE_PATH, AGG_RATE, AGG_LEVEL, DATA_ID)

NUM_EPOCHS=5

metrics = ['n_packets', 'n_bytes', 'sum_n_dest_ip', 'sum_n_dest_asn', 'sum_n_dest_ports', 'dir_ratio_packets', 'avg_duration']
z_scores = [10,10,10,10,10,10,10]
results = {}
for (metric, z) in zip(metrics, z_scores):
    print(metric)
    results[metric] = train_model(df, metric, get_model, NUM_EPOCHS, f"{AGG_LEVEL}_{str(DATA_ID)}", z)

show_prediction_graphs(results)

n_packets
Epoch 1/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 13s 126ms/step - loss: 0.8062 - root_mean_squared_error: 0.8974 - val_loss: 0.4325 - val_root_mean_squared_error: 0.6577
Epoch 2/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 119ms/step - loss: 0.6540 - root_mean_squared_error: 0.8066 - val_loss: 0.4321 - val_root_mean_squared_error: 0.6573
Epoch 3/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.6073 - root_mean_squared_error: 0.7772 - val_loss: 0.4281 - val_root_mean_squared_error: 0.6543
Epoch 4/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.6924 - root_mean_squared_error: 0.8300 - val_loss: 0.4174 - val_root_mean_squared_error: 0.6461
Epoch 5/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 11s 118ms/step - loss: 0.6977 - root_mean_squared_error: 0.8341 - val_loss: 0.4273 - val_root_mean_squared_error: 0.6537
94/94 ━━━━━━━━━━━━━━━━━━━━ 3s 36ms/step
42/42 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 2s 36ms/step
n_bytes
Epoch 1/5
94/94 ━━━━━━━━━━━━━━━━━━━━ 12s 120ms/step - loss: 0.9246 - roo

In [79]:
# Evaluation metrics table

eval_metrics_df = get_eval_metrics_df(results)

pd.options.display.width = 0  # Prevent line wrapping
pd.options.display.max_columns = None  # Show all columns
pd.options.display.float_format = "{:.2f}".format  # Format floats with 2 decimal places
print(eval_metrics_df.to_string(index=True))

Metrics                         n_packets                              n_bytes              sum_n_dest_ip            sum_n_dest_asn            sum_n_dest_ports             dir_ratio_packets              avg_duration           
Evaluation metrics                   RMSE  SMAPE     R^2                  RMSE  SMAPE   R^2          RMSE SMAPE  R^2           RMSE SMAPE  R^2             RMSE SMAPE   R^2              RMSE  SMAPE   R^2         RMSE SMAPE  R^2
Train Not-Inversed                   0.69  96.68   -0.82                  0.72 110.93 -2.19          0.12 58.96 0.88           0.18 69.93 0.71             0.29 65.24  0.54              0.88 142.53 -6.45         0.18 64.17 0.80
Train Inversed            124785674430.17  40.91   -0.82 102451448666778144.00  53.34 -2.19     169971.85  9.71 0.88        5259.27  7.87 0.71          1947.97 10.46  0.54              0.00  11.96 -6.45         1.47  8.41 0.80
Validation Not-Inversed              0.43  99.34   -0.53                  0.54 115.05 -2.12 